In [74]:
import numpy as np
import pandas as pd
import re
import nltk
from nltk.tokenize import word_tokenize
from nltk.corpus import stopwords
nltk.download('stopwords')
nltk.download('punkt')
nltk.download('averaged_perceptron_tagger')
nltk.download('wordnet')
nltk.download('omw-1.4')
from nltk.tokenize import word_tokenize
from nltk.stem import SnowballStemmer
from nltk.corpus import wordnet
from nltk.stem import WordNetLemmatizer

[nltk_data] Downloading package stopwords to
[nltk_data]     C:\Users\476196\AppData\Roaming\nltk_data...
[nltk_data]   Package stopwords is already up-to-date!
[nltk_data] Downloading package punkt to
[nltk_data]     C:\Users\476196\AppData\Roaming\nltk_data...
[nltk_data]   Package punkt is already up-to-date!
[nltk_data] Downloading package averaged_perceptron_tagger to
[nltk_data]     C:\Users\476196\AppData\Roaming\nltk_data...
[nltk_data]   Package averaged_perceptron_tagger is already up-to-
[nltk_data]       date!
[nltk_data] Downloading package wordnet to
[nltk_data]     C:\Users\476196\AppData\Roaming\nltk_data...
[nltk_data]   Package wordnet is already up-to-date!
[nltk_data] Downloading package omw-1.4 to
[nltk_data]     C:\Users\476196\AppData\Roaming\nltk_data...
[nltk_data]   Package omw-1.4 is already up-to-date!


In [2]:
df=pd.read_excel("Injury Triage 2022.xlsx")
pd.set_option('display.max_rows',None)
#pd.set_option('display.max_colwidth',None)
df.head()

Report Reference Date of Hire [Injury/Illness Investigation]  \
0     INJ/74328-21                                  2015-06-08   
1     INJ/77946-21                                  2018-11-19   
2     INJ/78901-21                                  1985-05-22   
3     INJ/78920-21                                  2001-03-05   
4     INJ/79016-21                                  2016-12-19   

   Years of Service at incident  Employee Age [Injury/Illness Investigation]  \
0                      5.791781                                         41.0   
1                      2.876712                                         31.0   
2                     36.515068                                         65.0   
3                     20.397260                                         45.0   
4                      4.928767                                         26.0   

   Employee PPR Number Employee Station/Base  Employee Department  \
0           92625800.0                   MSP                  125   
1           98143400.0                   MSP                  120   
2           41398400.0                   MSP                  120   
3           49806300.0                   SLC                  120   
4           86271500.0                   LGA                  125   

  Specific Site (Value Only)    Severity Direct Cause (Value/Other)  \
0             Ticket Counter  Negligible           Lifting/Carrying   
1             On A/C at Ramp       Minor           Lifting/Carrying   
2           Bagroom Outbound       Minor        Walking Down Stairs   
3                       Ramp       Minor          Walking Up Stairs   
4                 Ramp Other       Minor        Walking Down Stairs   

         Root Cause                               Description of Event  \
0     Human Factors  Had a large family with all heavy bags. pick u...   
1        Ergonomics  while loading bags into cart at inbound flight...   
2     Human Factors  Agent was walking up and down stairs in bagroo...   
3     Human Factors  On July 23, 2021 at approximately 0630, the EE...   
4  Work Environment  Agent was assisting a passenger deplaning from...   

  OSHA Recordability Date to Recordable Incident Date      ACS Category  \
0    OSHA Recordable         2022-06-09    2021-03-22      Ergo - Lobby   
1    OSHA Recordable         2022-03-08    2021-10-04  Ergo - Ramp Bags   
2    OSHA Recordable         2022-02-01    2021-11-17      Stepping Up    
3    OSHA Recordable         2022-01-02    2021-07-23       Stepping Up   
4    OSHA Recordable         2022-01-03    2021-11-22     Stepping Down   

  Bag Touchpoint Step      ACS Solution Secondary Solution  
0                   1         Jog Belts                NaN  
1                   8  BW Ergo Training                NaN  
2                 NaN               TBD                NaN  
3                 NaN               TBD                NaN  
4                 NaN               TBD                NaN

In [3]:
df.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 720 entries, 0 to 719
Data columns (total 19 columns):
 #   Column                                       Non-Null Count  Dtype         
---  ------                                       --------------  -----         
 0   Report Reference                             720 non-null    object        
 1   Date of Hire [Injury/Illness Investigation]  719 non-null    datetime64[ns]
 2   Years of Service at incident                 720 non-null    float64       
 3   Employee Age [Injury/Illness Investigation]  719 non-null    float64       
 4   Employee PPR Number                          719 non-null    float64       
 5   Employee Station/Base                        720 non-null    object        
 6   Employee Department                          720 non-null    int64         
 7   Specific Site (Value Only)                   719 non-null    object        
 8   Severity                                     720 non-null    object        
 9  

In [4]:
df.shape

(720, 19)

In [5]:
df['ACS Category'].value_counts()

Ergo - Ramp Bags            83
Ergo - Bagroom              83
Slip, Trip, Fall            72
Ergo - Stacking in Bin      69
Ergo - Lobby                65
Global Clean                36
Situational Awareness       27
A/C Door                    21
Ergo - Stacking In Bins     17
Head Strike                 15
Stepping Up/Down            13
Ergo - Stacking in Bins     13
Ergo - Cart Pull/Push       13
Struck By                   12
Environmental               10
Hitching                     9
Stepping Down                9
Repetitive Motion            7
Human Remains Induced        6
Walking                      6
UNK                          6
Vehicle Collision            6
A/C Door                     4
Struck By GSE                4
Stepping Up/ Down            4
Ergo - Cart Pull / Push      4
Wheel Chair                  4
Passenger / Pet Induced      4
Office Induced               4
Clutter                      4
Clean                        4
Tow Bar Induced              4
Walking 

In [6]:
df['Severity'].value_counts()

Minor         670
Moderate       30
-              10
Negligible      7
Major           3
Name: Severity, dtype: int64

In [7]:
df['OSHA Recordability'].value_counts()

OSHA Recordable    720
Name: OSHA Recordability, dtype: int64

In [8]:
df['Specific Site (Value Only)'].value_counts()

Ramp                          252
Bagroom Outbound               93
Ticket Counter                 70
Other                          30
Gate Area                      27
Ramp - Not at Gate             27
Inside Cargo Bin               27
Bagroom Inbound                26
Cabin Service - Stock Room     22
Jetway, Interior, Stairs       21
Ramp Other                     17
Lobby Area                     10
A/C Door                        9
Baggage/Luggage Service         8
Sky Club                        8
On A/C at Ramp                  8
Terminal Other                  7
In A/C at Ramp                  6
Concourse                       5
E Con GSE Shop                  5
Bag/Luggage Belt/Conveyor       5
Bag/Luggage Claim Area          4
Roadway                         3
Office Area                     3
Elevator/Escalator              2
Dock                            2
Aircraft Belly                  2
Stairway                        2
Ground Trans/Shuttle            2
Training Class

In [9]:
df['Bag Touchpoint Step'].value_counts()

2              64
1              57
5              33
9              15
6              14
8A             12
3              12
8              12
10             10
4               9
6,7             9
3A              8
3 through 8     7
5a              6
5A              5
2 thru 8        5
2 thru 9        5
7               5
8a              4
3 thru 9        4
6A              4
4,5             3
3b              2
3 thru 8        2
5 thru 7        2
4,5,6,7         2
4 thru 7        2
5,6             2
5B              2
3B              2
2 thru 9        2
                1
8C              1
6a              1
05A             1
4 , 5           1
3 Thru 8        1
3c              1
3,4             1
3,7,8,9         1
2,8             1
4,6             1
2 or 9          1
3C              1
Name: Bag Touchpoint Step, dtype: int64

In [10]:
df['Direct Cause (Value/Other)'].value_counts()

Lifting/Carrying                                                                                                                                                                                                                                                                                                                                                   214
Slip/Trip/Fall - Same Level                                                                                                                                                                                                                                                                                                                                         51
Struck Against/Bumped Into                                                                                                                                                                                                                                                                

In [11]:
df['Root Cause'].value_counts()

Human Factors                    261
Ergonomics                       210
Other                             73
People/Job Procedures             57
Work Environment                  49
Equipment                         17
Personal Protective Equipment      9
Industrial Hygiene                 2
Name: Root Cause, dtype: int64

In [12]:
df[['Years of Service at incident','Employee Age [Injury/Illness Investigation]','Employee Department','Specific Site (Value Only)','Severity','Direct Cause (Value/Other)','Root Cause','Description of Event','ACS Category']]

Years of Service at incident  \
0                        5.791781   
1                        2.876712   
2                       36.515068   
3                       20.397260   
4                        4.928767   
5                        2.542466   
6                       43.786301   
7                        0.235616   
8                       14.347945   
9                       26.109589   
10                       0.243836   
11                       0.150685   
12                      24.109589   
13                       0.435616   
14                       7.465753   
15                       7.583562   
16                      15.402740   
17                       0.227397   
18                      25.383562   
19                       4.646575   
20                      24.808219   
21                       7.046575   
22                      35.583562   
23                      11.046575   
24                       3.542466   
25                      20.857534   
26                      15.402740   
27                       0.150685   
28                       7.438356   
29                       4.827397   
30                       2.550685   
31                      15.350685   
32                      25.816438   
33                      37.498630   
34                       0.515068   
35                       2.926027   
36                       3.326027   
37                      26.109589   
38                       2.427397   
39                       2.356164   
40                       0.534247   
41                       7.512329   
42                       1.895890   
43                       2.490411   
44                       0.134247   
45                       0.273973   
46                       0.295890   
47                       6.720548   
48                       3.953425   
49                       6.128767   
50                      11.890411   
51                      25.701370   
52                      10.257534   
53                      14.600000   
54                      14.638356   
55                      14.994521   
56                      26.624658   
57                       0.556164   
58                      19.778082   
59                      23.493151   
60                      24.652055   
61                       2.939726   
62                      23.983562   
63                       4.498630   
64                      28.172603   
65                      24.802740   
66                       4.690411   
67                       0.413699   
68                       3.619178   
69                       4.660274   
70                       0.369863   
71                      23.558904   
72                       5.068493   
73                       3.189041   
74                       6.761644   
75                       0.065753   
76                      36.104110   
77                       0.271233   
78                       6.416438   
79                      14.553425   
80                       2.980822   
81                       0.328767   
82                       2.687671   
83                       0.098630   
84                       3.065753   
85                      27.312329   
86                      12.504110   
87                       1.947945   
88                       2.693151   
89                       8.980822   
90                       2.164384   
91                       0.473973   
92                       0.178082   
93                       0.315068   
94                      15.112329   
95                       0.191781   
96                       0.205479   
97                      21.219178   
98                       7.909589   
99                       3.632877   
100                     23.701370   
101                     22.832877   
102                      0.287671   
103                     24.758904   
104                      0.649315   
105                     14.958904   
106                      0.367123   
107      

In [13]:
df['Employee Department'].value_counts()

120    462
125    175
139     52
127      9
587      8
613      8
118      5
110      1
Name: Employee Department, dtype: int64

In [14]:
df[df['Employee Department']==110]

Report Reference Date of Hire [Injury/Illness Investigation]  \
543     INJ/83184-22                                  2011-01-03   

     Years of Service at incident  \
543                     11.364384   

     Employee Age [Injury/Illness Investigation]  Employee PPR Number  \
543                                         36.0           88241400.0   

    Employee Station/Base  Employee Department Specific Site (Value Only)  \
543                   ATL                  110         Communication Area   

    Severity Direct Cause (Value/Other)             Root Cause  \
543    Minor                  Struck By  People/Job Procedures   

                                  Description of Event OSHA Recordability  \
543  Flare up of old injury when heavy photo equipm...    OSHA Recordable   

    Date to Recordable Incident Date ACS Category Bag Touchpoint Step  \
543         2022-05-18    2022-05-13      unknown                 NaN   

    ACS Solution Secondary Solution  
543          TBD                NaN

In [15]:
df[df['Employee Department']==118]

Report Reference Date of Hire [Injury/Illness Investigation]  \
125     INJ/80309-22                                  1995-03-20   
180     INJ/80750-22                                  1995-08-14   
267     INJ/81264-22                                  1989-08-19   
394     INJ/82063-22                                  1996-07-29   
432     INJ/82381-22                                  2021-10-18   

     Years of Service at incident  \
125                     26.857534   
180                     26.520548   
267                     32.569863   
394                     25.682192   
432                      0.490411   

     Employee Age [Injury/Illness Investigation]  Employee PPR Number  \
125                                         50.0           27352300.0   
180                                         46.0           56834800.0   
267                                         52.0           24191400.0   
394                                         59.0           10568400.0   
432                                         22.0           42771700.0   

    Employee Station/Base  Employee Department Specific Site (Value Only)  \
125                   MSP                  118                Office Area   
180                   DTW                  118         Ramp - Not at Gate   
267                   MCO                  118         Elevator/Escalator   
394                   ATL                  118            Office Building   
432                   LGA                  118                      Other   

    Severity        Direct Cause (Value/Other)     Root Cause  \
125    Minor                  Lifting/Carrying     Ergonomics   
180    Minor  Slip/Trip/Fall - Different Level          Other   
267    Minor               Defective Equipment      Equipment   
394    Minor        Struck Against/Bumped Into          Other   
432    Minor                  Twisting/Turning  Human Factors   

                                  Description of Event OSHA Recordability  \
125  At beginning of shift, agent was adjusting com...    OSHA Recordable   
180  While stepping out of the SafeAero Deice truck...    OSHA Recordable   
267  At 0850, EE called ACC stating that while he w...    OSHA Recordable   
394  Reaching down to scan his badge when another p...    OSHA Recordable   
432  Agent was walking down the slope and tripped o...    OSHA Recordable   

    Date to Recordable Incident Date           ACS Category  \
125         2022-01-25    2022-01-20         Office Induced   
180         2022-02-14    2022-02-13       Slip, Trip, Fall   
267         2022-03-07    2022-03-07         Airport Design   
394         2022-04-13    2022-03-29  Situational Awareness   
432         2022-04-25    2022-04-15       Slip, Trip, Fall   

    Bag Touchpoint Step ACS Solution Secondary Solution  
125                 NaN          TBD                NaN  
180                 NaN        Shoes                NaN  
267                 NaN          UNK                NaN  
394                 NaN          TBD                NaN  
432                 NaN          TBD                NaN

In [16]:
df[['Specific Site (Value Only)','Employee Department']]

Specific Site (Value Only)  Employee Department
0                Ticket Counter                  125
1                On A/C at Ramp                  120
2              Bagroom Outbound                  120
3                          Ramp                  120
4                    Ramp Other                  125
5                      A/C Door                  125
6              Inside Cargo Bin                  120
7               Bagroom Inbound                  120
8                      A/C Door                  125
9                Ticket Counter                  125
10                         Ramp                  120
11                     A/C Door                  125
12             Inside Cargo Bin                  120
13                         Ramp                  120
14                         Ramp                  120
15                         Ramp                  120
16              Bagroom Inbound                  120
17               Ticket Counter                  125
18               Ticket Counter                  125
19                         Ramp                  120
20                         Ramp                  120
21     Jetway, Interior, Stairs                  125
22                         Ramp                  120
23               Ticket Counter                  125
24               Ticket Counter                  125
25             Bagroom Outbound                  120
26                    Gate Area                  125
27           Ramp - Not at Gate                  120
28               Ticket Counter                  125
29                    Gate Area                  125
30               Terminal Other                  125
31                         Ramp                  120
32      Baggage/Luggage Service                  125
33             Bagroom Outbound                  120
34               Ticket Counter                  125
35                    Gate Area                  120
36             Bagroom Outbound                  120
37               Ticket Counter                  125
38               Terminal Other                  125
39             Bagroom Outbound                  120
40                         Ramp                  120
41                         Ramp                  120
42                    Concourse                  125
43           Ramp - Not at Gate                  120
44                         Ramp                  120
45           Ramp - Not at Gate                  120
46                         Ramp                  120
47                   Ramp Other                  120
48                         Ramp                  120
49                     Stairway                  125
50      Baggage/Luggage Service                  125
51                   Ramp Other                  120
52                         Ramp                  120
53     Jetway, Interior, Stairs                  125
54                         Ramp                  120
55                         Ramp                  120
56                         Ramp                  120
57             Bagroom Outbound                  120
58                         Ramp                  120
59                         Ramp                  120
60                    Gate Area                  125
61                         Ramp                  120
62                         Ramp                  120
63                         Ramp                  120
64                    Gate Area                  125
65                         Ramp                  120
66             Bagroom Outbound                  120
67                         Ramp                  120
68               Remote Parking                  120
69                         Ramp                  120
70             Bagroom Outbound                  120
71             Bagroom Outbound                  120
72                   Lobby Area                  125
73                         Ramp                  120
74             Inside Cargo Bi

In [17]:
pd.set_option('display.max_colwidth',None)

In [18]:
df[['Description of Event','ACS Category']]

Description of Event  \
0                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                      Had a large family with all heavy bags. pick up a 61LBS when to twisted to place bag on the belt from scale. pain in left lower back. The EE has been continuing treatment in HCM since DOI, and was moved to prevention but was still being seen/treated for lingering pain and discomfort. On 6/3/22 the ee reaggravated the old injury (by same mechanism, lifting heavy bags) to the point where, after being treated in HCM a couple more times, she decided to see a provider.   
1                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                  while loading bags into cart at inbound flight right lower back strained   
2                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                            Agent was walking up and down stairs in bagroom and felt a burning feeling on the inside of his right knee, stating it became sore to walk on.   
3                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                          

In [19]:
df['Incident Date'].min()

Timestamp('2021-03-22 00:00:00')

In [20]:
df['Incident Date'].max()

Timestamp('2022-06-30 00:00:00')

In [21]:
df['Date to Recordable'].min()

Timestamp('2022-01-02 00:00:00')

In [22]:
df['Date to Recordable'].max()

Timestamp('2022-07-08 00:00:00')

In [23]:
df[['Incident Date','Date to Recordable']].sort_values(by='Incident Date')

Incident Date Date to Recordable
0      2021-03-22         2022-06-09
335    2021-07-07         2022-04-07
137    2021-07-13         2022-02-02
3      2021-07-23         2022-01-02
83     2021-08-11         2022-02-01
72     2021-09-01         2022-02-04
171    2021-09-01         2022-02-13
272    2021-10-02         2022-03-11
1      2021-10-04         2022-03-08
61     2021-10-06         2022-01-12
116    2021-10-16         2022-01-21
65     2021-11-04         2022-01-31
85     2021-11-09         2022-01-19
2      2021-11-17         2022-02-01
4      2021-11-22         2022-01-03
84     2021-11-28         2022-01-12
75     2021-12-02         2022-01-18
8      2021-12-02         2022-01-02
66     2021-12-03         2022-01-19
5      2021-12-03         2022-01-04
6      2021-12-03         2022-01-04
147    2021-12-06         2022-02-08
7      2021-12-08         2022-01-13
9      2021-12-09         2022-01-07
15     2021-12-09         2022-01-04
262    2021-12-10         2022-04-06
10     2021-12-11         2022-01-08
13     2021-12-11         2022-01-03
27     2021-12-12         2022-01-04
17     2021-12-12         2022-01-04
11     2021-12-12         2022-01-06
69     2021-12-13         2022-01-19
246    2021-12-14         2022-03-17
12     2021-12-14         2022-01-14
32     2021-12-14         2022-01-03
19     2021-12-15         2022-02-22
45     2021-12-16         2022-01-04
14     2021-12-16         2022-01-27
21     2021-12-16         2022-01-07
16     2021-12-17         2022-01-06
25     2021-12-17         2022-01-07
18     2021-12-17         2022-01-04
20     2021-12-18         2022-01-05
24     2021-12-18         2022-01-04
22     2021-12-19         2022-01-05
23     2021-12-20         2022-01-03
26     2021-12-21         2022-01-14
31     2021-12-23         2022-01-05
417    2021-12-24         2022-04-22
28     2021-12-26         2022-01-03
29     2021-12-26         2022-01-07
36     2021-12-26         2022-01-07
153    2021-12-26         2022-04-05
30     2021-12-27         2022-01-03
86     2021-12-27         2022-01-19
64     2021-12-27         2022-01-07
34     2021-12-27         2022-01-10
380    2021-12-27         2022-04-04
110    2021-12-28         2022-01-19
77     2021-12-28         2022-01-10
109    2021-12-29         2022-01-19
56     2021-12-29         2022-01-06
106    2021-12-29         2022-01-18
33     2021-12-30         2022-01-04
37     2021-12-30         2022-01-19
47     2021-12-30         2022-01-06
46     2021-12-30         2022-01-10
136    2021-12-31         2022-01-26
38     2021-12-31         2022-01-07
35     2021-12-31         2022-01-04
54     2021-12-31         2022-01-10
39     2022-01-02         2022-01-13
42     2022-01-02         2022-01-10
40     2022-01-02         2022-01-09
52     2022-01-02         2022-01-24
43     2022-01-02         2022-01-04
55     2022-01-02         2022-01-05
41     2022-01-02         2022-06-21
53     2022-01-02         2022-01-05
76     2022-01-03         2022-01-12
49     2022-01-03         2022-01-19
94     2022-01-03         2022-02-03
97     2022-01-03         2022-01-15
44     2022-01-03         2022-01-03
57     2022-01-03         2022-01-17
59     2022-01-03         2022-01-11
51     2022-01-04         2022-01-13
50     2022-01-04         2022-01-06
48     2022-01-04         2022-01-07
73     2022-01-05         2022-01-11
58     2022-01-05         2022-01-12
60     2022-01-06         2022-01-06
108    2022-01-06         2022-01-26
111    2022-01-06         2022-02-04
67     2022-01-07         2022-01-12
78     2022-01-07         2022-01-11
62     2022-01-07         2022-01-11
63     2022-01-07         2022-01-11
74     2022-01-07         2022-01-19
120    2022-01-07         2022-01-21
68     2022-01-08         2022-01-10
71     2022-01-08         2022-01-21
70     2022-01-08         2022-01-10
90     2022-01-09         2022-01-24
87     2022-01-09         2022-01-18
80     2022-01-09         2022-01-18
79     2022-01-09         2022-01-11
91     2

In [24]:
#Number of words in a description
df['word_count'] = df['Description of Event'].apply(lambda x:len(str(x).split()))

In [25]:
df[['Description of Event','word_count']]

Description of Event  \
0                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                      Had a large family with all heavy bags. pick up a 61LBS when to twisted to place bag on the belt from scale. pain in left lower back. The EE has been continuing treatment in HCM since DOI, and was moved to prevention but was still being seen/treated for lingering pain and discomfort. On 6/3/22 the ee reaggravated the old injury (by same mechanism, lifting heavy bags) to the point where, after being treated in HCM a couple more times, she decided to see a provider.   
1                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                  while loading bags into cart at inbound flight right lower back strained   
2                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                            Agent was walking up and down stairs in bagroom and felt a burning feeling on the inside of his right knee, stating it became sore to walk on.   
3                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                          

In [30]:
#convert to lowercase, strip and remove punctuations
def preprocess(text):
    text=text.lower()
    text=text.strip()
    text=re.compile('<.*?>').sub('',text)
    text=re.sub('\s+',' ',text)
    text=re.sub(r'\[[0-9]*\]',' ',text)
    text=re.sub(r'[^\w\s]','',str(text).lower().strip())
    text=re.sub(r'\s+',' ',text)
    return text

In [33]:
df['clean_text'] = df['Description of Event'].apply(lambda x:preprocess(x))
df[['Description of Event','clean_text']]

Description of Event  \
0                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                      Had a large family with all heavy bags. pick up a 61LBS when to twisted to place bag on the belt from scale. pain in left lower back. The EE has been continuing treatment in HCM since DOI, and was moved to prevention but was still being seen/treated for lingering pain and discomfort. On 6/3/22 the ee reaggravated the old injury (by same mechanism, lifting heavy bags) to the point where, after being treated in HCM a couple more times, she decided to see a provider.   
1                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                  while loading bags into cart at inbound flight right lower back strained   
2                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                            Agent was walking up and down stairs in bagroom and felt a burning feeling on the inside of his right knee, stating it became sore to walk on.   
3                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                          

In [57]:
#stopword removal
def stopword(string):
    a=[i for i in string.split() if i not in stopwords.words('english')]
    return ' '.join(a) # remove multiple whitespaces

In [60]:
df['clean_text'] = df['Description of Event'].apply(lambda x:stopword(x))
df[['Description of Event','clean_text']]

Description of Event  \
0                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                      Had a large family with all heavy bags. pick up a 61LBS when to twisted to place bag on the belt from scale. pain in left lower back. The EE has been continuing treatment in HCM since DOI, and was moved to prevention but was still being seen/treated for lingering pain and discomfort. On 6/3/22 the ee reaggravated the old injury (by same mechanism, lifting heavy bags) to the point where, after being treated in HCM a couple more times, she decided to see a provider.   
1                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                  while loading bags into cart at inbound flight right lower back strained   
2                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                            Agent was walking up and down stairs in bagroom and felt a burning feeling on the inside of his right knee, stating it became sore to walk on.   
3                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                          

In [62]:
#Lemmatization -converting a work to its base form
wl=WordNetLemmatizer()
def get_wordnet_pos(tag):
    if tag.startswith('J'):
        return wordnet.ADJ
    elif tag.startswith('V'):
        return wordnet.VERB
    elif tag.startswith('N'):
        return wordnet.NOUN
    elif tag.startswith('R'):
        return wordnet.ADV
    else:
        return wordnet.NOUN

In [63]:
#Tokenize the sentence
def lemmatizer(string):
    word_pos_tags = nltk.pos_tag(word_tokenize(string)) # get position tags
    #Map the position tag and lemmatize the word/token
    a=[wl.lemmatize(tag[0],get_wordnet_pos(tag[1])) for idx,tag in enumerate(word_pos_tags)]
    return " ".join(a)

In [64]:
def finalpreprocess(string):
    return lemmatizer(stopword(preprocess(string)))

In [73]:
df['clean_text']=df['Description of Event'].apply(lambda x:finalpreprocess(x))
df[['Description of Event','clean_text']]

Description of Event  \
0                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                      Had a large family with all heavy bags. pick up a 61LBS when to twisted to place bag on the belt from scale. pain in left lower back. The EE has been continuing treatment in HCM since DOI, and was moved to prevention but was still being seen/treated for lingering pain and discomfort. On 6/3/22 the ee reaggravated the old injury (by same mechanism, lifting heavy bags) to the point where, after being treated in HCM a couple more times, she decided to see a provider.   
1                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                  while loading bags into cart at inbound flight right lower back strained   
2                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                            Agent was walking up and down stairs in bagroom and felt a burning feeling on the inside of his right knee, stating it became sore to walk on.   
3                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                          